In [1]:
import pandas as pd
import numpy as np
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten
from keras.utils import np_utils
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import confusion_matrix

data = pd.read_csv('nor.csv')  # 載入正規化後的資料
ydata = data['SALARY_CLASS']  # data y
xdata = data[['AGE', 'FG', 'FGA', 'FG%', '3P', '3PA', '3P%',
    '2P', '2PA', '2P%', 'eFG%', 'FT', 'FTA', 'FT%', 'ORB', 'DRB', 'TRB',
    'AST', 'STL', 'BLK', 'TOV', 'PF', 'POINTS', 'GP', 'MPG', 'ORPM',
    'DRPM', 'RPM', 'WINS_RPM', 'PIE', 'PACE', 'W']]  # data x

C:\Users\user\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [2]:
position = ['PG', 'C', 'SF', 'SG', 'PF']
px = []
py = []
for p in position:
    a = xdata[data['POSITION'].isin([p])]
    a.reset_index(drop=True, inplace=True)
    b = ydata[data['POSITION'].isin([p])]
    b.reset_index(drop=True, inplace=True)
    px.append(np.array(a))
    py.append(np.array(b))

In [3]:
skf = StratifiedKFold(n_splits=5, random_state=None, shuffle=True)  # 將資料按照label比例分出train data和test data(分成5種)
r = 20  # range
td1 = []
td2 = []
ac = []
cf = []
for i in range(len(position)):
    print('位置:', position[i])
    accuracy = 0  # 計算平均accuracy
    trainDataLen = 0  # 計算平均train data大小
    testDataLen = 0  # 計算平均test data大小
    confusion = np.zeros([3, 3])  # 計算平均confusion matrix
    for rr in range(r):
        print('第', rr, '輪')
        model = Sequential()
        model.add(Dense(units=128, input_dim=32, kernel_initializer='normal', activation='relu'))
        model.add(Dropout(0.1))
        model.add(Dense(units=512, kernel_initializer='normal', activation='relu'))
        model.add(Dropout(0.1))
        model.add(Dense(units=1024, kernel_initializer='normal', activation='relu'))
        model.add(Dropout(0.1))
        model.add(Dense(units=3, kernel_initializer='normal', activation='softmax'))
        model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
        for train_index, test_index in skf.split(px[i], py[i]):
            trainDataLen = trainDataLen + len(train_index)
            testDataLen = testDataLen + len(test_index)
            y_TrainOneHot = np_utils.to_categorical(py[i][train_index])
            y_TestOneHot = np_utils.to_categorical(py[i][test_index])
            train_history = model.fit(x=px[i][train_index], y=y_TrainOneHot, validation_split=0.1, epochs=100, verbose=1)
            scores = model.evaluate(px[i][test_index], y_TestOneHot)
            accuracy = accuracy + scores[1]
            y_predict = model.predict_classes(px[i][test_index])
            confusion = confusion + confusion_matrix(py[i][test_index], y_predict)
    td1.append(trainDataLen / (r * 5))
    td2.append(testDataLen / (r * 5))
    ac.append(accuracy * 100.0 / (r * 5))
    cf.append(confusion / (r * 5))

位置: PG
第 0 輪
Train on 47 samples, validate on 6 samples
Epoch 1/100
47/47 [==============================] - 1s 12ms/step - loss: 1.0794 - accuracy: 0.3617 - val_loss: 1.2126 - val_accuracy: 0.1667
Epoch 2/100
47/47 [==============================] - 0s 705us/step - loss: 0.9892 - accuracy: 0.5106 - val_loss: 1.3456 - val_accuracy: 0.1667
Epoch 3/100
47/47 [==============================] - 0s 701us/step - loss: 0.9466 - accuracy: 0.5106 - val_loss: 1.4132 - val_accuracy: 0.1667
Epoch 4/100
47/47 [==============================] - 0s 685us/step - loss: 0.9116 - accuracy: 0.5532 - val_loss: 1.3508 - val_accuracy: 0.1667
Epoch 5/100
47/47 [==============================] - 0s 679us/step - loss: 0.8480 - accuracy: 0.6596 - val_loss: 1.2158 - val_accuracy: 0.1667
Epoch 6/100
47/47 [==============================] - 0s 715us/step - loss: 0.8129 - accuracy: 0.6170 - val_loss: 1.0910 - val_accuracy: 0.1667
Epoch 7/100
47/47 [==============================] - 0s 628us/step - loss: 0.7391 - acc

47/47 [==============================] - 0s 638us/step - loss: 0.1967 - accuracy: 0.8936 - val_loss: 0.9302 - val_accuracy: 0.8333
Epoch 58/100
47/47 [==============================] - 0s 659us/step - loss: 0.1939 - accuracy: 0.8723 - val_loss: 0.9492 - val_accuracy: 0.8333
Epoch 59/100
47/47 [==============================] - 0s 639us/step - loss: 0.1690 - accuracy: 0.9787 - val_loss: 0.9791 - val_accuracy: 0.8333
Epoch 60/100
47/47 [==============================] - 0s 720us/step - loss: 0.1799 - accuracy: 0.9362 - val_loss: 0.9644 - val_accuracy: 0.8333
Epoch 61/100
47/47 [==============================] - 0s 711us/step - loss: 0.1419 - accuracy: 0.9362 - val_loss: 0.9754 - val_accuracy: 0.8333
Epoch 62/100
47/47 [==============================] - 0s 799us/step - loss: 0.1547 - accuracy: 0.9149 - val_loss: 1.0018 - val_accuracy: 0.8333
Epoch 63/100
47/47 [==============================] - 0s 870us/step - loss: 0.2352 - accuracy: 0.9149 - val_loss: 1.0296 - val_accuracy: 0.8333
Epoch

47/47 [==============================] - 0s 727us/step - loss: 0.0957 - accuracy: 0.9574 - val_loss: 1.3400 - val_accuracy: 0.8333
Epoch 14/100
47/47 [==============================] - 0s 649us/step - loss: 0.1227 - accuracy: 0.9574 - val_loss: 1.3388 - val_accuracy: 0.6667
Epoch 15/100
47/47 [==============================] - 0s 797us/step - loss: 0.0890 - accuracy: 0.9787 - val_loss: 1.3441 - val_accuracy: 0.6667
Epoch 16/100
47/47 [==============================] - 0s 712us/step - loss: 0.0784 - accuracy: 0.9574 - val_loss: 1.3614 - val_accuracy: 0.8333
Epoch 17/100
47/47 [==============================] - 0s 725us/step - loss: 0.0590 - accuracy: 1.0000 - val_loss: 1.3898 - val_accuracy: 0.8333
Epoch 18/100
47/47 [==============================] - 0s 706us/step - loss: 0.0740 - accuracy: 0.9787 - val_loss: 1.4256 - val_accuracy: 0.8333
Epoch 19/100
47/47 [==============================] - 0s 702us/step - loss: 0.0631 - accuracy: 1.0000 - val_loss: 1.4334 - val_accuracy: 0.8333
Epoch

Epoch 70/100
47/47 [==============================] - 0s 728us/step - loss: 0.0031 - accuracy: 1.0000 - val_loss: 1.7539 - val_accuracy: 0.8333
Epoch 71/100
47/47 [==============================] - 0s 732us/step - loss: 0.0178 - accuracy: 1.0000 - val_loss: 1.7130 - val_accuracy: 0.8333
Epoch 72/100
47/47 [==============================] - 0s 666us/step - loss: 0.0795 - accuracy: 0.9574 - val_loss: 1.8750 - val_accuracy: 0.8333
Epoch 73/100
47/47 [==============================] - 0s 690us/step - loss: 0.0439 - accuracy: 0.9787 - val_loss: 2.1288 - val_accuracy: 0.8333
Epoch 74/100
47/47 [==============================] - 0s 685us/step - loss: 0.0334 - accuracy: 1.0000 - val_loss: 2.2138 - val_accuracy: 0.8333
Epoch 75/100
47/47 [==============================] - 0s 701us/step - loss: 0.0410 - accuracy: 0.9787 - val_loss: 2.0095 - val_accuracy: 0.8333
Epoch 76/100
47/47 [==============================] - 0s 696us/step - loss: 0.0055 - accuracy: 1.0000 - val_loss: 1.8270 - val_accuracy:

Epoch 26/100
48/48 [==============================] - 0s 605us/step - loss: 0.0238 - accuracy: 1.0000 - val_loss: 1.8115 - val_accuracy: 0.8333
Epoch 27/100
48/48 [==============================] - 0s 693us/step - loss: 0.0414 - accuracy: 0.9792 - val_loss: 1.8646 - val_accuracy: 0.8333
Epoch 28/100
48/48 [==============================] - 0s 718us/step - loss: 0.0283 - accuracy: 1.0000 - val_loss: 1.9003 - val_accuracy: 0.8333
Epoch 29/100
48/48 [==============================] - 0s 732us/step - loss: 0.0096 - accuracy: 1.0000 - val_loss: 1.9008 - val_accuracy: 0.8333
Epoch 30/100
48/48 [==============================] - 0s 681us/step - loss: 0.0091 - accuracy: 1.0000 - val_loss: 1.8941 - val_accuracy: 0.8333
Epoch 31/100
48/48 [==============================] - 0s 728us/step - loss: 0.0075 - accuracy: 1.0000 - val_loss: 1.8739 - val_accuracy: 0.8333
Epoch 32/100
48/48 [==============================] - 0s 730us/step - loss: 0.0157 - accuracy: 1.0000 - val_loss: 1.8805 - val_accuracy:

...

49/49 [==============================] - 0s 2ms/step - loss: 0.0211 - accuracy: 1.0000 - val_loss: 0.0902 - val_accuracy: 1.0000
Epoch 21/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0535 - accuracy: 0.9796 - val_loss: 0.0643 - val_accuracy: 1.0000
Epoch 22/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0421 - accuracy: 0.9796 - val_loss: 0.0446 - val_accuracy: 1.0000
Epoch 23/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0310 - accuracy: 1.0000 - val_loss: 0.1439 - val_accuracy: 0.8333
Epoch 24/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0981 - accuracy: 0.9796 - val_loss: 0.0314 - val_accuracy: 1.0000
Epoch 25/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0275 - accuracy: 0.9796 - val_loss: 0.0699 - val_accuracy: 1.0000
Epoch 26/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0261 - accuracy: 1.0000 - val_loss: 0.1613 - val_accuracy: 1.0000
Epoch 27/100
49/49 

Epoch 78/100
49/49 [==============================] - 0s 3ms/step - loss: 0.0045 - accuracy: 1.0000 - val_loss: 0.0946 - val_accuracy: 1.0000
Epoch 79/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0525 - accuracy: 0.9796 - val_loss: 0.0587 - val_accuracy: 1.0000
Epoch 80/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0092 - accuracy: 1.0000 - val_loss: 0.0479 - val_accuracy: 1.0000
Epoch 81/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0054 - accuracy: 1.0000 - val_loss: 0.0439 - val_accuracy: 1.0000
Epoch 82/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0076 - accuracy: 1.0000 - val_loss: 0.0480 - val_accuracy: 1.0000
Epoch 83/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0494 - accuracy: 0.9796 - val_loss: 0.0542 - val_accuracy: 1.0000
Epoch 84/100
49/49 [==============================] - 0s 719us/step - loss: 0.0168 - accuracy: 1.0000 - val_loss: 0.0789 - val_accuracy: 1.0000
Epoc

49/49 [==============================] - 0s 1ms/step - loss: 0.0414 - accuracy: 0.9796 - val_loss: 0.0157 - val_accuracy: 1.0000
Epoch 36/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0876 - accuracy: 0.9796 - val_loss: 0.0157 - val_accuracy: 1.0000
Epoch 37/100
49/49 [==============================] - 0s 1ms/step - loss: 0.0128 - accuracy: 1.0000 - val_loss: 0.0155 - val_accuracy: 1.0000
Epoch 38/100
49/49 [==============================] - 0s 1ms/step - loss: 0.1007 - accuracy: 0.9796 - val_loss: 0.0118 - val_accuracy: 1.0000
Epoch 39/100
49/49 [==============================] - 0s 1ms/step - loss: 0.0169 - accuracy: 1.0000 - val_loss: 0.0203 - val_accuracy: 1.0000
Epoch 40/100
49/49 [==============================] - 0s 1ms/step - loss: 0.0026 - accuracy: 1.0000 - val_loss: 0.0391 - val_accuracy: 1.0000
Epoch 41/100
49/49 [==============================] - 0s 1ms/step - loss: 0.0126 - accuracy: 1.0000 - val_loss: 0.0519 - val_accuracy: 1.0000
Epoch 42/100
49/49 

Epoch 93/100
49/49 [==============================] - 0s 1ms/step - loss: 0.0139 - accuracy: 1.0000 - val_loss: 0.0850 - val_accuracy: 1.0000
Epoch 94/100
49/49 [==============================] - 0s 2ms/step - loss: 0.0075 - accuracy: 1.0000 - val_loss: 0.0770 - val_accuracy: 1.0000
Epoch 95/100
49/49 [==============================] - 0s 1ms/step - loss: 0.0050 - accuracy: 1.0000 - val_loss: 0.0708 - val_accuracy: 1.0000
Epoch 96/100
49/49 [==============================] - 0s 1ms/step - loss: 8.3442e-04 - accuracy: 1.0000 - val_loss: 0.0664 - val_accuracy: 1.0000
Epoch 97/100
49/49 [==============================] - 0s 1ms/step - loss: 0.0014 - accuracy: 1.0000 - val_loss: 0.0631 - val_accuracy: 1.0000
Epoch 98/100
49/49 [==============================] - 0s 1ms/step - loss: 0.0061 - accuracy: 1.0000 - val_loss: 0.0580 - val_accuracy: 1.0000
Epoch 99/100
49/49 [==============================] - 0s 1ms/step - loss: 0.0043 - accuracy: 1.0000 - val_loss: 0.0514 - val_accuracy: 1.0000
Ep

Epoch 50/100
51/51 [==============================] - 0s 1ms/step - loss: 0.0018 - accuracy: 1.0000 - val_loss: 0.0018 - val_accuracy: 1.0000
Epoch 51/100
51/51 [==============================] - 0s 1ms/step - loss: 0.0333 - accuracy: 0.9804 - val_loss: 0.0031 - val_accuracy: 1.0000
Epoch 52/100
51/51 [==============================] - 0s 1ms/step - loss: 0.0261 - accuracy: 0.9804 - val_loss: 0.0033 - val_accuracy: 1.0000
Epoch 53/100
51/51 [==============================] - 0s 1ms/step - loss: 0.0017 - accuracy: 1.0000 - val_loss: 0.0326 - val_accuracy: 1.0000
Epoch 54/100
51/51 [==============================] - 0s 1ms/step - loss: 0.0052 - accuracy: 1.0000 - val_loss: 0.1688 - val_accuracy: 0.8333
Epoch 55/100
51/51 [==============================] - 0s 2ms/step - loss: 0.0550 - accuracy: 0.9804 - val_loss: 0.1022 - val_accuracy: 1.0000
Epoch 56/100
51/51 [==============================] - 0s 917us/step - loss: 0.0091 - accuracy: 1.0000 - val_loss: 0.0058 - val_accuracy: 1.0000
Epoc

In [4]:
print('trainDataLen:', td1, 'testDataLen:', td2)
print("Accuracy:", ac)
print('confusion:\n', cf)

trainDataLen: [54.4, 52.8, 51.2, 53.6, 55.2] testDataLen: [13.6, 13.2, 12.8, 13.4, 13.8]
Accuracy: [86.1285719871521, 77.86337059736252, 82.58241841197014, 83.0558608174324, 86.40000012516975]
confusion:
 [array([[2.92, 0.65, 0.03],
       [0.45, 5.52, 0.43],
       [0.07, 0.37, 3.16]]), array([[1.07, 1.21, 0.12],
       [0.35, 5.65, 0.6 ],
       [0.06, 0.74, 3.4 ]]), array([[2.19, 0.59, 0.02],
       [0.3 , 5.2 , 0.7 ],
       [0.05, 0.67, 3.08]]), array([[2.82, 0.7 , 0.08],
       [0.2 , 6.32, 0.48],
       [0.06, 0.82, 1.92]]), array([[2.79, 0.38, 0.03],
       [0.39, 6.98, 0.43],
       [0.  , 0.74, 2.06]])]
